In [1]:
import pandas as pd

In [2]:
all_trades = pd.read_parquet('../data/all_trades_profitability.parquet')

In [4]:
all_trades["creation_date"] = all_trades["creation_timestamp"].dt.date

In [5]:
all_trades = all_trades.sort_values(
    by="creation_timestamp", ascending=True
)

all_trades["month_year_week"] = (
    all_trades["creation_timestamp"].dt.to_period("W").dt.strftime("%b-%d")
)

/var/folders/gp/02mb1d514ng739czlxw1lhh00000gn/T/ipykernel_38171/1825242321.py:6: UserWarning: Converting to PeriodArray/Index representation will drop timezone information.
  all_trades["creation_timestamp"].dt.to_period("W").dt.strftime("%b-%d")


In [6]:
def compute_winning_metric_per_trader_per_market_creator(
    trader_address: str, week_traders_data: pd.DataFrame, market_creator: str = "all"
) -> float:
    assert "market_creator" in week_traders_data.columns
    filtered_traders_data = week_traders_data.loc[
        week_traders_data["trader_address"] == trader_address
    ]
    if market_creator != "all":  # compute only for the specific market creator
        filtered_traders_data = filtered_traders_data.loc[
            filtered_traders_data["market_creator"] == market_creator
        ]
        if len(filtered_traders_data) == 0:
            return None  # No Data
    winning_perc = (
        filtered_traders_data["winning_trade"].sum()
        / filtered_traders_data["winning_trade"].count()
        * 100.0
    )
    return winning_perc

In [7]:
def merge_winning_metrics_by_trader(
    trader: str, weekly_data: pd.DataFrame, week: str
) -> pd.DataFrame:
    trader_metrics = []
    # computation as specification 1 for all market creators
    winning_metrics_all = {}
    winning_metric_all = compute_winning_metric_per_trader_per_market_creator(
        trader, weekly_data, market_creator="all"
    )
    winning_metrics_all["winning_perc"] = winning_metric_all
    winning_metrics_all["month_year_week"] = week
    winning_metrics_all["market_creator"] = "all"
    trader_metrics.append(winning_metrics_all)
    if week == "Jul-21":
        print(f"trader = {trader}, win_perc for all ={winning_metric_all}")

    # computation as specification 1 for quickstart markets
    winning_metrics_qs = {}
    winning_metric = compute_winning_metric_per_trader_per_market_creator(
        trader, weekly_data, market_creator="quickstart"
    )
    if winning_metric:
        winning_metrics_qs["winning_perc"] = winning_metric
        winning_metrics_qs["month_year_week"] = week
        winning_metrics_qs["market_creator"] = "quickstart"
        trader_metrics.append(winning_metrics_qs)

    # computation as specification 1 for pearl markets
    winning_metrics_pearl = {}
    winning_metric = compute_winning_metric_per_trader_per_market_creator(
        trader, weekly_data, market_creator="pearl"
    )
    if winning_metric:
        winning_metrics_pearl["winning_perc"] = winning_metric
        winning_metrics_pearl["month_year_week"] = week
        winning_metrics_pearl["market_creator"] = "pearl"
        trader_metrics.append(winning_metrics_pearl)

    result = pd.DataFrame.from_dict(trader_metrics, orient="columns")
    # tqdm.write(f"Total length of all winning metrics for this week = {len(result)}")
    return result

In [27]:
def win_metrics_trader_level(weekly_data):
    winning_trades = (
        weekly_data.groupby(["month_year_week", "market_creator","trader_address"], sort=False)[
            "winning_trade"
        ].sum()
        / weekly_data.groupby(["month_year_week", "market_creator","trader_address"], sort=False)[
            "winning_trade"
        ].count()
        * 100
    )
    # winning_trades is a series, give it a dataframe
    winning_trades = winning_trades.reset_index()
    winning_trades.columns = winning_trades.columns.astype(str)
    winning_trades.columns = ["month_year_week", "market_creator", "trader_address", "winning_trade"]
    winning_trades.rename(columns={"winning_trade": "winning_perc"})
    return winning_trades

In [28]:
from tqdm import tqdm

market_all = all_trades.copy(deep=True)
market_all["market_creator"] = "all"

# merging both dataframes
final_traders = pd.concat([market_all, all_trades], ignore_index=True)
final_traders = final_traders.sort_values(
        by="creation_timestamp", ascending=True)


winning_df = win_metrics_trader_level(final_traders)
winning_df.head()

month_year_week market_creator                              trader_address  \
0          Jul-21            all  0x95ecc70d9f4feb162ed9f41c4432d990c36c8f57   
1          Jul-21     quickstart  0x95ecc70d9f4feb162ed9f41c4432d990c36c8f57   
2          Jul-21     quickstart  0xf089874165be0377680683fd5187a058dea82683   
3          Jul-21            all  0xf089874165be0377680683fd5187a058dea82683   
4          Jul-21     quickstart  0x49f4e3d8edc85efda9b0a36d96e406a59b13fcc2   

   winning_trade  
0      33.333333  
1      33.333333  
2     100.000000  
3     100.000000  
4      50.000000

In [ ]:
winning_df = compute_winning_metrics_by_trader(all_trades)

In [29]:
winning_pearl = winning_df.loc[winning_df["market_creator"]=="pearl"]

In [30]:
winning_pearl.head()

month_year_week market_creator                              trader_address  \
7           Jul-21          pearl  0xe283e408c6017447da9fe092d52c386753699680   
29          Jul-21          pearl  0x913dedfcfb335a49509b67acb3b1ab2612a5c0c9   
30          Jul-21          pearl  0x1b9e28e7f817e1312636a485f31cca8a4be61fac   
33          Jul-21          pearl  0xe0113a139f591efa8bf5e19308c7c27199682d77   
37          Jul-21          pearl  0x66a022b113b41e08d90cfd9468b8b6565d6ea995   

    winning_trade  
7             0.0  
29          100.0  
30            0.0  
33            0.0  
37          100.0